*Copyright (c) Cornac Authors. All rights reserved.*

*Licensed under the Apache 2.0 License.*

# Model Ensembling

<table class="tfo-notebook-buttons" align="left">
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/PreferredAI/cornac/blob/master/tutorials/model_ensembling.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />Run in Google Colab</a>
  </td>
  <td>
    <a target="_blank" href="https://github.com/PreferredAI/cornac/blob/master/tutorials/model_ensembling.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png" />View source on GitHub</a>
  </td>
</table>

This notebook provides an example of how to ensemble multiple recommendation models in Cornac.

Ensemble models is a technique that combines the predictions of multiple models to produce a single prediction. The idea is that by combining the predictions of multiple models, we can improve the overall performance of the recommendation system.

We will use the MovieLens 100K dataset and ensemble 2 models.

** Note: ** Part of this notebook (in Section 4) uses the `scikit-learn` package. 

## 1. Setup

### 1.1 Install required dependencies

In [41]:
! pip install seaborn scikit-learn cornac==2.2.2 tensorflow==2.12.0

Defaulting to user installation because normal site-packages is not writeable
ERROR: Could not find a version that satisfies the requirement tensorflow==2.12.0 (from versions: 2.16.0rc0, 2.16.1, 2.16.2, 2.17.0rc0, 2.17.0rc1, 2.17.0, 2.18.0rc0, 2.18.0rc1)
ERROR: No matching distribution found for tensorflow==2.12.0


In [42]:
from IPython.display import display
import numpy as np
import pandas as pd
from tqdm import tqdm

from cornac.datasets import movielens
from cornac.models import BPR, WMF
from cornac.eval_methods import RatioSplit
from cornac.metrics import Precision, Recall
from cornac.utils import cache
from cornac import Experiment

from sklearn import linear_model
from sklearn.ensemble import RandomForestRegressor

## 2. Prepare Experiment

### 2.1 Loading Dataset

First, we load the MovieLens 100K dataset.

In [43]:
data = movielens.load_feedback(variant="100K") # Load MovieLens Dataset

rs = RatioSplit(data, test_size=0.2, seed=42, verbose=True) # Split to train-test set to 80-20
train_set, test_set = rs.train_set, rs.test_set

rating_threshold = 1.0
exclude_unknowns = True
---
Training data:
Number of users = 943
Number of items = 1651
Number of ratings = 80000
Max rating = 5.0
Min rating = 1.0
Global mean = 3.5
---
Test data:
Number of users = 943
Number of items = 1651
Number of ratings = 19964
Number of unknown users = 0
Number of unknown items = 0
---
Total users = 943
Total items = 1651


### 2.2 Training BPR and WMF models

We will train two models: 

1. BPR (Bayesian Personalized Ranking)
2. WMF (Weighted Matrix Factorization)

In [44]:
bpr_model = BPR(k=10, max_iter=100, learning_rate=0.01, lambda_reg=0.001) # Initialize BPR model
wmf_model = WMF(k=10, max_iter=300, a=1.0, b=0.1, learning_rate=0.001, lambda_u=0.01, lambda_v=0.01,) # Initialize WMF model

models = [bpr_model, wmf_model]
metrics = [Precision(k=50), Recall(k=50)] # Set metrics for experiment

experiment = Experiment(rs, models, metrics, user_based=True).run() # Run Experiment to compare BPR model to WMF model individually


[BPR] Training started!

[BPR] Evaluation started!


Ranking: 100%|██████████| 940/940 [00:00<00:00, 2435.38it/s]
I0000 00:00:1728842711.120252    6738 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355



[WMF] Training started!


100%|██████████| 300/300 [00:04<00:00, 66.94it/s, loss=174]


Learning completed!

[WMF] Evaluation started!


Ranking: 100%|██████████| 940/940 [00:00<00:00, 1832.92it/s]


TEST:
...
    | Precision@50 | Recall@50 | Train (s) | Test (s)
--- + ------------ + --------- + --------- + --------
BPR |       0.1811 |    0.5081 |    0.2325 |   0.3898
WMF |       0.1731 |    0.5064 |    4.5399 |   0.5149



Comparing Precision and Recall, both BPR and WMF are providing comparable results.

Let's move on to try to interpret these results by using the genres of movies that were recommended to us.

Generally, we could assume that if an individual likes a particular film genre like 'Romance', the recommender system should provide more of such 'Romance' films.

### 2.3 Interpreting Results

##### Creating a Movie Genre Dataframe

In [45]:
# Creating a dataframe of movies with its corresponding genres

# Download some information of MovieLens 100K dataset
item_df = pd.read_csv(
  cache("http://files.grouplens.org/datasets/movielens/ml-100k/u.item"), 
  sep="|", encoding="ISO-8859-1",
  names=["ItemID", "Title", "Release Date", "Video Release Date", "IMDb URL", 
         "unknown", "Action", "Adventure", "Animation", "Children's", "Comedy", 
         "Crime", "Documentary", "Drama", "Fantasy", "Film-Noir", "Horror", 
         "Musical", "Mystery", "Romance", "Sci-Fi", "Thriller", "War", "Western"]
).set_index("ItemID").drop(columns=["Video Release Date", "IMDb URL", "unknown"])

item_idx2id = train_set.item_ids # create a item index to film ID mapping
user_idx2id = train_set.user_ids

# Let's take a look at an example of this dataframe
display(item_df.head(3))


Title Release Date  Action  Adventure  Animation  \
ItemID                                                                 
1        Toy Story (1995)  01-Jan-1995       0          0          1   
2        GoldenEye (1995)  01-Jan-1995       1          1          0   
3       Four Rooms (1995)  01-Jan-1995       0          0          0   

        Children's  Comedy  Crime  Documentary  Drama  Fantasy  Film-Noir  \
ItemID                                                                      
1                1       1      0            0      0        0          0   
2                0       0      0            0      0        0          0   
3                0       0      0            0      0        0          0   

        Horror  Musical  Mystery  Romance  Sci-Fi  Thriller  War  Western  
ItemID                                                                     
1            0        0        0        0       0         0    0        0  
2            0        0        0        0       0         1    0        0  
3            0        0        0        0       0         1    0        0

The `item_df` dataframe consists of all movie items with its corresponding genre attributes.

Further down below, we are going to filter this table with the recommendations that we get from the recommender system models we created to get a better sense of its performance.

##### Creating Training Data Dataframe

To get a sense of what data has been inserted into our model for training, let's count the genres of the training data used to train the model.

But first, let's create a `training_data_df` dataframe with all training data.

The training data consists of 80000 triplets of **User Index**, **Item Index** and **Rating** rows as seen in the dataset summary in Section 2.1.

In [46]:
# Let's view a sample of the training data dataframe
print("Sample row of record:")
print("(user_index, item_index, rating):", list(zip(*train_set.uir_tuple))[0])

# Create a training data dataframe
training_data_df = pd.DataFrame(zip(*train_set.uir_tuple)) # adding all training data into dataframe
training_data_df.columns = ['user_idx', 'item_idx', 'rating'] # adding column names to the data

# Add new column, 'item_id', for further filtering in later sections
training_data_df['item_id'] = training_data_df.apply(lambda row: item_idx2id[int(row['item_idx'])], axis=1) # converted from the item index field

Sample row of record:
(user_index, item_index, rating): (0, 0, 4.0)


##### Filtering Training Data

Let's filter based on a particular user to learn more about the user.

We set ``UIDX`` to user index **3**, and ``TOPK`` to **50**, to get the top 50 recommendations in each model for comparison.

In [47]:
UIDX = 3
TOPK = 50

In [48]:
# Filter training data (rating = 5.0 and user index = UIDX)
filter_df = training_data_df[(training_data_df['rating'] == 5.0) & (training_data_df['user_idx'] == UIDX)]
filter_df = item_df.loc[[int(item_id) for item_id in filter_df["item_id"]]] # get genres of movie items

print("Number of movies:", len(filter_df))

# Group by Movie Genre and Sum by genres
filter_df = filter_df.select_dtypes(np.number).sum() 
filter_df = filter_df.to_frame("Sum") # Let's call that column 'Sum'

# Add a new column '%' for the percentage of individual genre sum compared to total sum
filter_df["%"] = filter_df["Sum"] / filter_df["Sum"].sum() * 100
filter_df["%"] = filter_df["%"].round(1)

# Let's see the training data genres, sums and percentages
print("Movies rated 5.0 by user index 3 in training data")
display(filter_df.sort_values("Sum", ascending=False))

Number of movies: 138
Movies rated 5.0 by user index 3 in training data


Sum     %
Drama         71  24.9
Comedy        39  13.7
Romance       32  11.2
Action        30  10.5
Thriller      29  10.2
Adventure     19   6.7
War           15   5.3
Crime         12   4.2
Sci-Fi         9   3.2
Mystery        8   2.8
Children's     5   1.8
Horror         5   1.8
Musical        4   1.4
Animation      2   0.7
Film-Noir      2   0.7
Western        2   0.7
Documentary    1   0.4
Fantasy        0   0.0

As shown above in the training data, the top genres for user index 3 with movies rated 5.0 include 'Drama', 'Comedy', 'Romance', 'Action' and 'Thriller'.

Let's now compare them to the recommendations of the BPR and WMF models respectively.

##### Interpreting Recommendations of BPR, WMF Models

In [49]:
# Get the Top 5 Genres in filtered training data for user index 3
top_genres = filter_df.sort_values("Sum", ascending=False).head(5).index.tolist()
print("\nTop 5 Genres in training data:", top_genres)

# Get top K recommendations for BPR and put them into the genre dataframe
bpr_recommendations, bpr_scores = bpr_model.rank(UIDX, k=TOPK) # rank recommendations by score, limit to top K
print(len(bpr_recommendations))
bpr_topk = [item_idx2id[iidx] for iidx in bpr_recommendations[:TOPK]] # convert item indexes into item ids
bpr_df = item_df.loc[[int(iid) for iid in bpr_topk]] # filter the movie genre dataframe by item ids

# Let's view the top recommendations for BPR by top genres
display("BPR: Top recommendations", bpr_df[["Title"] + top_genres].head(10))

# Now, let's do likewise for WMF - get top K recommendations and put them into the genre dataframe
wmf_recommendations, wmf_scores = wmf_model.rank(UIDX, k=TOPK) # rank recommendations by score
wmf_topk = [item_idx2id[iidx] for iidx in wmf_recommendations[:TOPK]] # convert item indexes into item ids
wmf_df = item_df.loc[[int(iid) for iid in wmf_topk]] # filter the movie genre dataframe by item ids

# View the top recommendations for WMF
display("WMF: Top recommendations", wmf_df[["Title"] + top_genres].head(10))


Top 5 Genres in training data: ['Drama', 'Comedy', 'Romance', 'Action', 'Thriller']
1651


'BPR: Top recommendations'

Title  Drama  Comedy  Romance  Action  \
ItemID                                                                    
300                Air Force One (1997)      0       0        0       1   
245             Devil's Own, The (1997)      1       0        0       1   
328            Conspiracy Theory (1997)      0       0        1       1   
313                      Titanic (1997)      1       0        1       1   
237                Jerry Maguire (1996)      1       0        1       0   
471           Courage Under Fire (1996)      1       0        0       0   
282              Time to Kill, A (1996)      1       0        0       0   
322               Murder at 1600 (1997)      0       0        0       0   
255     My Best Friend's Wedding (1997)      0       1        1       0   
15            Mr. Holland's Opus (1995)      1       0        0       0   

        Thriller  
ItemID            
300            1  
245            1  
328            1  
313            0  
237            0  
471            0  
282            0  
322            1  
255            0  
15             0

'WMF: Top recommendations'

Title  Drama  Comedy  Romance  Action  \
ItemID                                                                    
313                      Titanic (1997)      1       0        1       1   
50                     Star Wars (1977)      0       0        1       1   
181           Return of the Jedi (1983)      0       0        1       1   
588         Beauty and the Beast (1991)      0       0        0       0   
258                      Contact (1997)      1       0        0       0   
318             Schindler's List (1993)      1       0        0       0   
272            Good Will Hunting (1997)      1       0        0       0   
257                 Men in Black (1997)      0       1        0       1   
174      Raiders of the Lost Ark (1981)      0       0        0       1   
172     Empire Strikes Back, The (1980)      1       0        1       1   

        Thriller  
ItemID            
313            0  
50             0  
181            0  
588            0  
258            0  
318            0  
272            0  
257            0  
174            0  
172            0

Now that we have seen the top recommendations of the BPR and WMF models, let's do a comparison by taking a look at the genre distribution.

##### Comparing Models by Genre Distribution

In [50]:
# Let's introduce `combined_df` for comparison.
# This dataframe will be used to compare models by summing up genres from recommendations of different models
combined_df = pd.DataFrame({
    "Train Data %": filter_df["%"],
    "BPR Sum": bpr_df.select_dtypes(np.number).sum(), # group by genres, then get sum of each genre
    "WMF Sum": wmf_df.select_dtypes(np.number).sum() # likewise for WMF
})

# Get percentages of movie genre sums
combined_df['BPR %'] = combined_df['BPR Sum'] / combined_df['BPR Sum'].sum() * 100 
combined_df["WMF %"] = combined_df["WMF Sum"] / combined_df["WMF Sum"].sum() * 100

combined_df = combined_df.round(1) # round all 
combined_df = combined_df.sort_values("Train Data %", ascending=False)

# Let's take a look at the genre distribution by percentages
display("Train Data to Recommended % Distribution", combined_df[['Train Data %', 'BPR %', 'WMF %']])

'Train Data to Recommended % Distribution'

Train Data %  BPR %  WMF %
Drama                24.9   16.9   20.0
Comedy               13.7   11.3   12.0
Romance              11.2   14.5   10.4
Action               10.5   12.9   11.2
Thriller             10.2   16.1    4.8
Adventure             6.7    5.6    6.4
War                   5.3    7.3    6.4
Crime                 4.2    1.6    1.6
Sci-Fi                3.2    5.6    6.4
Mystery               2.8    4.0    1.6
Children's            1.8    0.8    8.0
Horror                1.8    0.8    0.0
Musical               1.4    0.0    5.6
Animation             0.7    0.8    4.8
Film-Noir             0.7    0.8    0.0
Western               0.7    0.8    0.0
Documentary           0.4    0.0    0.0
Fantasy               0.0    0.0    0.8

Now that we have seen the distribution of individual models, we are curious about what kind of distribution we will get from ensembling these models.

Let's see what happens when we ensemble these two models. 

## 2. Simple model ensembling by Borda Count

We will ensemble the two models using the Borda Count method. The Borda Count method is a simple voting method that ranks the items based on the sum of their ranks from each model.

Assuming that we have a list of 5 items, the Borda Count method works as follows:

1. For each model, rank the items from 1 to 5 based on the predicted scores.
2. Sum the ranks of each item across all models.
3. Sort the items based on the sum of their ranks.
4. The top-ranked item is the final recommendation.
5. Repeat the process for the next user.

Given the below example for a random user 123:

| Rank | Model 1 | Model 2 | Model 3 | Allocated Points (N - rank) |
|------|---------|---------|---------|-----------------------------|
| 1    | A       | D       | E       | 5 - 1 = 4                   |
| 2    | B       | C       | A       | 5 - 2 = 3                   |
| 3    | C       | A       | B       | 5 - 3 = 2                   |
| 4    | D       | B       | D       | 5 - 4 = 1                   |
| 5    | E       | E       | C       | 5 - 5 = 0                   |

Based on the allocated points for each of the items, we sum the points up to get our Borda Count.

| Item | Model 1 | Model 2 | Model 3 | Borda Count  |
|------|---------|---------|---------|--------------|
| A    | 4       | 2       | 3       | 9            |
| B    | 3       | 1       | 2       | 6            |
| C    | 2       | 3       | 0       | 5            |
| D    | 1       | 4       | 1       | 6            |
| E    | 0       | 0       | 4       | 4            |

New ranking: A > B, D > C > E


Lets implement this method below.

In [51]:
# Let's create a new dataframe to calculate ranking and borda count
rank_df = pd.DataFrame({
    "ItemID": item_idx2id,
})

total_items = len(rank_df) # 1651 items

# Obtain points (inverse of rank) of the items based on the BPR score
rank_df["BPR Score"] = bpr_scores
rank_df["BPR Rank"] = rank_df["BPR Score"].rank(ascending=False).astype(int) # Get Rank where 1 = Top recommendation
rank_df["BPR Points"] = total_items - rank_df["BPR Rank"] # Get points by calculating ('Total Item count' - 'Rank')

# Do likewise for WMF
rank_df["WMF Score"] = wmf_scores
rank_df["WMF Rank"] = rank_df["WMF Score"].rank(ascending=False).astype(int) # Get Rank where 1 = Top recommendation
rank_df["WMF Points"] = total_items - rank_df["WMF Rank"] # Get points by calculating ('Total Item count' - 'Rank')

# Get Borda Count by summing up points of BPR and WMF
rank_df["Borda Count"] = rank_df["BPR Points"] + rank_df["WMF Points"]

# Round decimal places for readability purposes
rank_df = rank_df.round(3)

# Now let's take a look at the table with Borda Count 
display(rank_df.head(5))

ItemID  BPR Score  BPR Rank  BPR Points  WMF Score  WMF Rank  WMF Points  \
0    381      1.176       464        1187      3.336       316        1335   
1    602     -0.306       826         825      2.431       587        1064   
2    431      0.756       563        1088      3.221       349        1302   
3    875      1.554       371        1280      2.058       709         942   
4    182      1.856       313        1338      3.269       339        1312   

   Borda Count  
0         2522  
1         1889  
2         2390  
3         2222  
4         2650

Now that we have Borda Count, let's rerank this list and to provide the ensembled model's recommendation.

In [52]:
# Introduce reranked dataframe for borda count
reranked_df = rank_df.sort_values("Borda Count", ascending=False)

# Let's take a look at the ensembled top 5 recommendations and their respective ranks
display("Re-ranked Top K Item recommendations", reranked_df.head(5))

'Re-ranked Top K Item recommendations'

ItemID  BPR Score  BPR Rank  BPR Points  WMF Score  WMF Rank  WMF Points  \
152    313      5.901         4        1647      6.268         1        1650   
92      50      4.390        20        1631      5.747         2        1649   
212    258      4.389        21        1630      5.416         5        1646   
129    300      6.181         1        1650      4.913        31        1620   
387    315      4.684        13        1638      5.031        23        1628   

     Borda Count  
152         3297  
92          3280  
212         3276  
129         3270  
387         3266

The top recommendation ItemID **181**, was ranked **7** on BPR and **12** on WMF.

By doing Borda Count, we are able to aggregate model recommendations.

Next, let's add the recommendations into the genre distribution dataframe to compare its results to the base models.

In [53]:
borda_count_topk = reranked_df["ItemID"].values[:TOPK] # Get top K (50) Item IDs

borda_df = item_df.loc[[int(i) for i in borda_count_topk]] # Filter genre data frame by the top item IDs

# Add Borda Count results into 'combined_df' dataframe for comparison
combined_df["Borda Count Sum"] = borda_df.select_dtypes(np.number).sum() # group by genre, and calculate sum of each genre
combined_df["Borda Count %"] = combined_df["Borda Count Sum"] / combined_df["Borda Count Sum"].sum() * 100 # Calculate percentage of sum to total
combined_df["Borda Count %"] = combined_df["Borda Count %"].round(1) # rounding for readability purposes

# Let's take a look at the genre distribution of train data, BPR, WMF and the newly added Borda Count
display("Borda Count Recommendations Distribution", combined_df[["Train Data %", "BPR %", "WMF %", "Borda Count %"]])

'Borda Count Recommendations Distribution'

Train Data %  BPR %  WMF %  Borda Count %
Drama                24.9   16.9   20.0           20.5
Comedy               13.7   11.3   12.0           13.1
Romance              11.2   14.5   10.4           16.4
Action               10.5   12.9   11.2           10.7
Thriller             10.2   16.1    4.8           10.7
Adventure             6.7    5.6    6.4            5.7
War                   5.3    7.3    6.4            6.6
Crime                 4.2    1.6    1.6            0.8
Sci-Fi                3.2    5.6    6.4            5.7
Mystery               2.8    4.0    1.6            2.5
Children's            1.8    0.8    8.0            2.5
Horror                1.8    0.8    0.0            0.8
Musical               1.4    0.0    5.6            0.8
Animation             0.7    0.8    4.8            1.6
Film-Noir             0.7    0.8    0.0            0.8
Western               0.7    0.8    0.0            0.0
Documentary           0.4    0.0    0.0            0.0
Fantasy               0.0    0.0    0.8            0.8

In the next section, we will further add more models to the ensemble.

## 3. Adding more models to the Borda Count ensemble

We can easily add more models to the ensemble by training them and adding them. One approach is to train a model with different initializations using different random seeds. By adding multiple similar models of different random seeds (`seed=123`), some models could perform better for a set of users, while other models could perform better for another set of users.

Another way is to change the number of latent factors `k`. By achieving better performance on a subset of data for each of the models, we are able to improve the performance of the ensembled model as a whole.

By ensembling these models, we could potentially achieve better performance when combined.

Let's try adding a few more similar models with different random seed initializations.

In [54]:
# WMF models with different seeds
wmf_model_123 = WMF(name="WMF_123", k=10, max_iter=300, a=1.0, b=0.1, learning_rate=0.001, lambda_u=0.01, lambda_v=0.01, seed=123)
wmf_model_456 = WMF(name="WMF_456", k=20, max_iter=300, a=1.0, b=0.1, learning_rate=0.001, lambda_u=0.01, lambda_v=0.01, seed=456)
wmf_model_789 = WMF(name="WMF_789", k=30, max_iter=300, a=1.0, b=0.1, learning_rate=0.001, lambda_u=0.01, lambda_v=0.01, seed=789)
wmf_model_888 = WMF(name="WMF_888", k=40, max_iter=300, a=1.0, b=0.1, learning_rate=0.001, lambda_u=0.01, lambda_v=0.01, seed=888)
wmf_model_999 = WMF(name="WMF_999", k=50, max_iter=300, a=1.0, b=0.1, learning_rate=0.001, lambda_u=0.01, lambda_v=0.01, seed=999)

models = [wmf_model_123, wmf_model_456, wmf_model_789, wmf_model_888, wmf_model_999]

# Let's run an experiment to take a look at how different these models are, with just different random seeds!
experiment = Experiment(rs, models, metrics, user_based=True).run()

I0000 00:00:1728842716.786497    6738 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355



[WMF_123] Training started!


100%|██████████| 300/300 [00:04<00:00, 66.27it/s, loss=173]


Learning completed!

[WMF_123] Evaluation started!


Ranking: 100%|██████████| 940/940 [00:00<00:00, 2318.00it/s]
I0000 00:00:1728842721.788446    6738 cuda_executor.cc:1015] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355


...


[WMF_999] Training started!


100%|██████████| 300/300 [00:05<00:00, 54.36it/s, loss=102] 


Learning completed!

[WMF_999] Evaluation started!


Ranking: 100%|██████████| 940/940 [00:00<00:00, 2080.94it/s]


TEST:
...
        | Precision@50 | Recall@50 | Train (s) | Test (s)
------- + ------------ + --------- + --------- + --------
WMF_123 |       0.1750 |    0.5103 |    4.5760 |   0.4074
WMF_456 |       0.1779 |    0.5220 |    4.7476 |   0.3685
WMF_789 |       0.1734 |    0.5129 |    5.0436 |   0.3515
WMF_888 |       0.1706 |    0.5031 |    5.3605 |   0.5335
WMF_999 |       0.1656 |    0.4944 |    5.5967 |   0.4539



Based on the results, we can see that even within the same model, the results can vary. 

Let's try ensembling all these models together into 1 single model by Borda Count, and look at its recommendations.

In [55]:
# Let's create a different dataframe to calculate ranking and borda count
rank_2_df = pd.DataFrame({
    "ItemID": item_idx2id,
})

# Add a column named 'Ensembled WMF Model'
rank_2_df["Ensembled WMF Model"] = 0

# Calculate the points (inverse of rank) for each of the models and accumulate them into the 'Enhanced Borda Count' column
for model in models:
    name = model.name
    recommendations, scores = model.rank(UIDX)
    rank_2_df[name + "_rating"] = scores
    rank_2_df[name + "_rank"] = rank_2_df[name + "_rating"].rank(ascending=False).astype(int)
    rank_2_df[name + "_points"] = total_items - rank_2_df[name + "_rank"]
    rank_2_df["Ensembled WMF Model"] = rank_2_df["Ensembled WMF Model"] + rank_2_df[name + "_points"]

# Round results for readability
rank_2_df = rank_2_df.round(3)

# Let's sort and view the top recommendations!
print("Model score calculation:")
display(rank_2_df[["Ensembled WMF Model"]].sort_values("Ensembled WMF Model", ascending=False).head(10))

Model score calculation:


Ensembled WMF Model
37                  8229
197                 8178
152                 8151
279                 8126
532                 8122
156                 8121
147                 8105
522                 8085
61                  8076
670                 8063

In [56]:
# Now, let's add them to the combined dataframe for comparison with earlier models
enhanced_borda_count_topk = list(rank_2_df.sort_values("Ensembled WMF Model", ascending=False)["ItemID"].values[:TOPK])
enhanced_borda_df = item_df.loc[[int(i) for i in enhanced_borda_count_topk]]

combined_df["Ensembled WMF Model Sum"] = enhanced_borda_df.select_dtypes(np.number).sum()
combined_df["Ensembled WMF Model %"] = combined_df["Ensembled WMF Model Sum"] / combined_df["Ensembled WMF Model Sum"].sum() * 100
combined_df["Ensembled WMF Model %"] = combined_df["Ensembled WMF Model %"].round(1)

# Let's compare the recommendation distribution
display("Combined Recommendations Distribution", combined_df[["Train Data %", "BPR %", "WMF %", "Borda Count %", "Ensembled WMF Model %"]])

'Combined Recommendations Distribution'

Train Data %  BPR %  WMF %  Borda Count %  Ensembled WMF Model %
Drama                24.9   16.9   20.0           20.5                   23.9
Comedy               13.7   11.3   12.0           13.1                   13.7
Romance              11.2   14.5   10.4           16.4                   15.4
Action               10.5   12.9   11.2           10.7                   10.3
Thriller             10.2   16.1    4.8           10.7                    6.8
Adventure             6.7    5.6    6.4            5.7                    7.7
War                   5.3    7.3    6.4            6.6                    4.3
Crime                 4.2    1.6    1.6            0.8                    5.1
Sci-Fi                3.2    5.6    6.4            5.7                    5.1
Mystery               2.8    4.0    1.6            2.5                    3.4
Children's            1.8    0.8    8.0            2.5                    1.7
Horror                1.8    0.8    0.0            0.8                    0.0
Musical               1.4    0.0    5.6            0.8                    0.0
Animation             0.7    0.8    4.8            1.6                    0.9
Film-Noir             0.7    0.8    0.0            0.8                    0.9
Western               0.7    0.8    0.0            0.0                    0.9
Documentary           0.4    0.0    0.0            0.0                    0.0
Fantasy               0.0    0.0    0.8            0.8                    0.0

Now that we have touched on simple borda count, let's see how we could use other methods and popular packages such as **scikit-learn** to do advanced model ensembling.

## 4. Model Ensembling via Regression Models

We could continue by thinking of this as a meta-learning problem. We could treat recommendations of each base model as features and train a meta-learner to predict the final recommendation.

This could be any ML model such as a Linear Regression, Random Forest, Gradient Boosting, or even a Neural Network.

In this example, we will use a simple Linear Regression model to predict the final recommendation.

We will teach a model to learn from the different outputs of the base models of WMF.

##### 4.1 Prepare Data

In [57]:
# First, lets create training and test data dataframes
training_df = pd.DataFrame(zip(*train_set.uir_tuple)) # Add 'User Index', 'Item Index', 'Rating' triples as records in dataframe
training_df.columns = ['user_idx', 'item_idx', 'ground_score'] # Set column names

# Get all possible user_index, item_index combinations, add them into dataframe for inference
all_df = pd.DataFrame({
    "user_idx": [user_idx for user_idx in range(train_set.num_users) for _ in range(train_set.num_items)],
    "item_idx": [item_idx for _ in range(train_set.num_users) for item_idx in range(train_set.num_items)],
})
all_df['item_id'] = all_df.apply(lambda row: item_idx2id[int(row['item_idx'])], axis=1) # Add 'Item ID' column into dataframe by converting 'Item Index' to 'Item ID'

# Lets get all the scores for the models trained in Part 3.

# For each model, we add individual predicted ratings by individual models to training and test dataframes
for model in models:
    name = model.name
    training_df[name + "_score"] = training_df.apply(lambda row: model.score(int(row['user_idx']), int(row['item_idx'])), axis=1) # for training
    all_df[name + "_score"] = all_df.apply(lambda row: model.score(int(row['user_idx']), int(row['item_idx'])), axis=1) # for inference

# Let's pick out the 5 features - predicted ratings from the 5 models trained
X_train = training_df[['WMF_123_score', 'WMF_456_score', 'WMF_789_score', 'WMF_888_score', 'WMF_999_score']]
y_train = training_df['ground_score'] # use ground truth to train this linear regression model
X_inference = all_df[['WMF_123_score', 'WMF_456_score', 'WMF_789_score', 'WMF_888_score', 'WMF_999_score']] # all data, used to predict values for ranking

display("Training features", X_train.head(3)) # predicting ratings as features
display("Target values", y_train.head(3)) # ground truth ratings
display("Inference Data", X_inference.head(3)) # all inference data

'Training features'

WMF_123_score  WMF_456_score  WMF_789_score  WMF_888_score  WMF_999_score
0       2.110018       3.753257       3.692900       3.763934       3.974546
1       2.791631       2.339661       2.418044       2.738071       3.102871
2       3.750932       3.537887       3.441126       3.396540       3.855725

'Target values'

0    4.0
1    3.0
2    4.0
Name: ground_score, dtype: float64

'Inference Data'

WMF_123_score  WMF_456_score  WMF_789_score  WMF_888_score  WMF_999_score
0       2.110018       3.753257       3.692900       3.763934       3.974546
1       0.807434      -0.628530      -0.064267      -0.289080      -0.587279
2       1.648493       1.840384       1.829896       1.870474       1.534385

Now that we have already prepared the data for fitting into a **scikit-learn** model, let's first try to train a Linear Regression model

##### 4.2 Fitting Linear Regression Model

In [58]:
# Let's now fit into a Linear Regression model
regr = linear_model.LinearRegression(fit_intercept=False) # force model to only use predictions from WMF models
regr.fit(X_train, y_train) # train the model

# Input: 5 base model predicted ratings. Output: final predicted rating based on linear regression
y_pred = regr.predict(X_inference) # Get predictions based on trained model

all_df["Linear Regression Prediction"] = y_pred # create a column in `test_df` for the predictions

# Get Top K ratings from predictions
all_df = all_df.sort_values("Linear Regression Prediction", ascending=False) # sort by predicted ratings
top_item_ids = all_df[all_df['user_idx'] == UIDX]['item_id'].values[:TOPK] # filter top K (50 as set in Section 2.3)

# Place them into the comparison distribution dataframe
linear_regression_df = item_df.loc[[int(i) for i in top_item_ids]] # Get genres of ratings
combined_df["Linear Regression Sum"] = linear_regression_df.select_dtypes(np.number).sum() # group by genre and sum them up
combined_df["Linear Regression %"] = combined_df["Linear Regression Sum"] / combined_df["Linear Regression Sum"].sum() * 100 # get percentages of (genre sum / whole sum)

combined_df["Linear Regression %"] = combined_df["Linear Regression %"].round(1) # round values for readability

print(regr.coef_)
print(regr.intercept_)

# Now let's take a look at how the genre distribution is
display("Combined Recommendations Distribution", combined_df[["Train Data %", "BPR %", "WMF %", "Borda Count %", "Ensembled WMF Model %", "Linear Regression %"]])

[-0.18445674 -0.13890123  0.1438685   0.43231982  0.86287963]
0.0


'Combined Recommendations Distribution'

Train Data %  BPR %  WMF %  Borda Count %  Ensembled WMF Model %  \
Drama                24.9   16.9   20.0           20.5                   23.9   
Comedy               13.7   11.3   12.0           13.1                   13.7   
Romance              11.2   14.5   10.4           16.4                   15.4   
Action               10.5   12.9   11.2           10.7                   10.3   
Thriller             10.2   16.1    4.8           10.7                    6.8   
Adventure             6.7    5.6    6.4            5.7                    7.7   
War                   5.3    7.3    6.4            6.6                    4.3   
Crime                 4.2    1.6    1.6            0.8                    5.1   
Sci-Fi                3.2    5.6    6.4            5.7                    5.1   
Mystery               2.8    4.0    1.6            2.5                    3.4   
Children's            1.8    0.8    8.0            2.5                    1.7   
Horror                1.8    0.8    0.0            0.8                    0.0   
Musical               1.4    0.0    5.6            0.8                    0.0   
Animation             0.7    0.8    4.8            1.6                    0.9   
Film-Noir             0.7    0.8    0.0            0.8                    0.9   
Western               0.7    0.8    0.0            0.0                    0.9   
Documentary           0.4    0.0    0.0            0.0                    0.0   
Fantasy               0.0    0.0    0.8            0.8                    0.0   

             Linear Regression %  
Drama                       27.6  
Comedy                       8.6  
Romance                     16.2  
Action                       6.7  
Thriller                     8.6  
Adventure                    7.6  
War                          4.8  
Crime                        4.8  
Sci-Fi                       4.8  
Mystery                      1.9  
Children's                   1.9  
Horror                       0.0  
Musical                      2.9  
Animation                    1.0  
Film-Noir                    1.9  
Western                      1.0  
Documentary                  0.0  
Fantasy                      0.0

Explanation, interpretation. Last model contributes the most >>

We have successfully fit into a Linear Regression model using the 5 WMF base models built on Cornac.

You could continue using different regression models on **scikit-learn** to further predict ratings.

In the section below, we will train a Random Forest model.

##### 4.3 Fitting Random Forest Model

We reuse the same training data. >> Technically can use any machine learning model.


In [59]:
# Let's now train a Random Forest model
randomforest_model = RandomForestRegressor(n_estimators=50, random_state=42) 
randomforest_model.fit(X_train, y_train) # Train the model

# Input: 5 base model predicted ratings. Output: final predicted rating based on random forest
y_pred = randomforest_model.predict(X_inference)

all_df["Random Forest Score"] = y_pred # create a column in `all_df` for the predictions

# Get Top K ratings from predictions
all_df = all_df.sort_values("Random Forest Score", ascending=False) # sort by predicted ratings
top_item_ids = all_df[all_df['user_idx'] == UIDX]['item_id'].values[:TOPK] # filter top K (50 as set in Section 2.3)

# Place them into the comparison distribution dataframe
random_forest_df = item_df.loc[[int(i) for i in top_item_ids]] # Get genres of ratings
combined_df["Random Forest Sum"] = random_forest_df.select_dtypes(np.number).sum() # group by genre and sum them up
combined_df["Random Forest %"] = combined_df["Random Forest Sum"] / combined_df["Random Forest Sum"].sum() * 100 # get percentages of (genre sum / whole sum)

combined_df["Random Forest %"] = combined_df["Random Forest %"].round(1) # round values for readability

# Now let's take a look at how the genre distribution is
display("Combined Recommendations Distribution", combined_df[["Train Data %", "BPR %", "WMF %", "Borda Count %", "Ensembled WMF Model %", "Linear Regression %", "Random Forest %"]])

'Combined Recommendations Distribution'

Train Data %  BPR %  WMF %  Borda Count %  Ensembled WMF Model %  \
Drama                24.9   16.9   20.0           20.5                   23.9   
Comedy               13.7   11.3   12.0           13.1                   13.7   
Romance              11.2   14.5   10.4           16.4                   15.4   
Action               10.5   12.9   11.2           10.7                   10.3   
Thriller             10.2   16.1    4.8           10.7                    6.8   
Adventure             6.7    5.6    6.4            5.7                    7.7   
War                   5.3    7.3    6.4            6.6                    4.3   
Crime                 4.2    1.6    1.6            0.8                    5.1   
Sci-Fi                3.2    5.6    6.4            5.7                    5.1   
Mystery               2.8    4.0    1.6            2.5                    3.4   
Children's            1.8    0.8    8.0            2.5                    1.7   
Horror                1.8    0.8    0.0            0.8                    0.0   
Musical               1.4    0.0    5.6            0.8                    0.0   
Animation             0.7    0.8    4.8            1.6                    0.9   
Film-Noir             0.7    0.8    0.0            0.8                    0.9   
Western               0.7    0.8    0.0            0.0                    0.9   
Documentary           0.4    0.0    0.0            0.0                    0.0   
Fantasy               0.0    0.0    0.8            0.8                    0.0   

             Linear Regression %  Random Forest %  
Drama                       27.6             16.3  
Comedy                       8.6             18.4  
Romance                     16.2              8.2  
Action                       6.7             11.2  
Thriller                     8.6             10.2  
Adventure                    7.6              4.1  
War                          4.8              1.0  
Crime                        4.8              5.1  
Sci-Fi                       4.8              5.1  
Mystery                      1.9              4.1  
Children's                   1.9              5.1  
Horror                       0.0              4.1  
Musical                      2.9              3.1  
Animation                    1.0              1.0  
Film-Noir                    1.9              2.0  
Western                      1.0              0.0  
Documentary                  0.0              0.0  
Fantasy                      0.0              1.0

What happened in Section 4 was that we trained a linear regression model and random forest model to learn from the different base models, adapting to the changes in features based on how these base models are configured to be.

---

Ensemble learning doesn't stop here. You could continue on by: 
- Trying different Cornac base models
- Trying different ensemble methods
- Tweaking around base models and different parameters within them

By having different base models with different specializations, model ensembling could leverage on the strengths of different models. Effectiveness of these models could depend on many factors such as diversity and quality of base models, dataset size and quality.

It is also important to note that while model ensembling theoretically provides superior performance, there could be instances where base models outperforms ensembled models. Model ensembling also requires more computational resources as well. Therefore, we should consider striking a balance between performanace and computational costs.

---

So what constitutes to a good ensembled model? Which base models and configurations are ideal? These are topics that require further experimentation and discussion.

## 5. Further Comparison

Based on section 4, we are only able to eyeball the results and compare them visually based on a **single user**.

We have only compared the genre distributions of the recommendations for a **single user**.

What if we want to compare the models based on **multiple users**?
We can do so by calculating the score of all users and item combinations, then the **Precision** and **Recall** of the predictions for each model.

Let's first create a dataframe to store the results of the models given **all users and items**.

In [61]:
rank_df = pd.DataFrame({
    "user_idx": all_df["user_idx"],
    "item_idx": all_df["item_idx"],
})

total_items = train_set.num_items # 1651 items

models_to_calculate = [bpr_model, wmf_model, wmf_model_123, wmf_model_456, wmf_model_789, wmf_model_888, wmf_model_999]

# Calculate points for each model using the Borda count process.
# Take note that points should be calculated on a per user basis.
for model in models_to_calculate:
    name = model.name
    rank_df[name + "_score"] = rank_df.apply(lambda row: model.score(int(row['user_idx']), int(row['item_idx'])), axis=1)
    point_list = [] # This list will be added into the dataframe later

    # Calculate points for each user
    for user_idx in range(train_set.num_users):
        sub_rank_df = rank_df[rank_df["user_idx"] == user_idx] # get all items for a user
        sub_rank_df[name + "_rank"] = sub_rank_df[name + "_score"].rank(ascending=False).astype(int) # Get Rank where 1 = Top recommendation
        sub_rank_df[name + "_points"] = total_items - sub_rank_df[name + "_rank"] # Get points by calculating ('Total Item count' - 'Rank')
        point_list.extend(sub_rank_df[name + "_points"].values.tolist()) # add points to list
    
    rank_df[name + "_points"] = point_list


display(rank_df.head(5)) # Now `rank_df` contains the points for each model

/tmp/ipykernel_6738/1088501630.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub_rank_df[name + "_rank"] = sub_rank_df[name + "_score"].rank(ascending=False).astype(int) # Get Rank where 1 = Top recommendation
/tmp/ipykernel_6738/1088501630.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sub_rank_df[name + "_points"] = total_items - sub_rank_df[name + "_rank"] # Get points by calculating ('Total Item count' - 'Rank')
/tmp/ipykernel_6738/1088501630.py:20: SettingWithCopyWarning: 
A value is tryin

user_idx  item_idx  BPR_score  BPR_points  WMF_score  WMF_points  \
573293       347       396   3.014429         332   2.056086         154   
613253       371       732   2.702705        1066   2.265926        1225   
143736        87        99  -0.207694        1097   1.055882         845   
570323       345       728  -3.052034         581  -1.497697         478   
564010       341      1019  -0.414165          41   0.173729         574   

        WMF_123_score  WMF_123_points  WMF_456_score  WMF_456_points  \
573293       2.128789             706       1.915834             832   
613253       2.413004            1047       1.922187             883   
143736       0.915166            1056       1.220583             856   
570323      -1.052202             224      -2.663744             776   
564010       0.364553             121       0.501006             499   

        WMF_789_score  WMF_789_points  WMF_888_score  WMF_888_points  \
573293       1.648838            1135       1.414293            1000   
613253       2.128542              37       1.960726              28   
143736       1.520252            1101       0.410065            1093   
570323      -1.312760            1270       1.110806            1104   
564010       0.238304             713       0.464368             806   

        WMF_999_score  WMF_999_points  
573293       1.823689             379  
613253       2.503561              99  
143736       1.133245            1341  
570323      -0.472541            1200  
564010       0.415116             820

Now that we have the points calculated. Let's add them up as per sections 2 and 3 above.

To reiterate, our simple Borda Count model consists of the **BPR Model** and **WMF Model**.

While the enhanced WMF model consists of multiple models: **wmf_model_123**, **wmf_model_456**, **wmf_model_789**, **wmf_model_888**, **wmf_model_999**, some of which have different initialization parameters.

In [62]:

borda_count_models = [bpr_model, wmf_model]
rank_df["Borda Count"] = rank_df[[model.name + "_points" for model in borda_count_models]].sum(axis=1) # Sum up points of BPR and WMF

enhanced_wmf_models = [wmf_model_123, wmf_model_456, wmf_model_789, wmf_model_888, wmf_model_999]
rank_df["Enhanced WMF Model"] = rank_df[[model.name + "_points" for model in enhanced_wmf_models]].sum(axis=1) # Sum up points of all WMF models

display(rank_df.head(5))

# Now, lets add them into the `all_df` dataframe for comparison
all_df.sort_values(by=["user_idx", "item_idx"], inplace=True) # ensure that the dataframe is sorted by user index and item index

all_df["BPR_score"] = rank_df["BPR_score"].values
all_df["WMF_score"] = rank_df["WMF_score"].values

all_df["Borda Count"] = rank_df["Borda Count"].values
all_df["Enhanced WMF Model"] = rank_df["Enhanced WMF Model"].values

display("`all_df` - Comparison of all Models", all_df.head(5))


user_idx  item_idx  BPR_score  BPR_points  WMF_score  WMF_points  \
573293       347       396   3.014429         332   2.056086         154   
613253       371       732   2.702705        1066   2.265926        1225   
143736        87        99  -0.207694        1097   1.055882         845   
570323       345       728  -3.052034         581  -1.497697         478   
564010       341      1019  -0.414165          41   0.173729         574   

        WMF_123_score  WMF_123_points  WMF_456_score  WMF_456_points  \
573293       2.128789             706       1.915834             832   
613253       2.413004            1047       1.922187             883   
143736       0.915166            1056       1.220583             856   
570323      -1.052202             224      -2.663744             776   
564010       0.364553             121       0.501006             499   

        WMF_789_score  WMF_789_points  WMF_888_score  WMF_888_points  \
573293       1.648838            1135       1.414293            1000   
613253       2.128542              37       1.960726              28   
143736       1.520252            1101       0.410065            1093   
570323      -1.312760            1270       1.110806            1104   
564010       0.238304             713       0.464368             806   

        WMF_999_score  WMF_999_points  Borda Count  Enhanced WMF Model  
573293       1.823689             379          486                4052  
613253       2.503561              99         2291                2094  
143736       1.133245            1341         1942                5447  
570323      -0.472541            1200         1059                4574  
564010       0.415116             820          615                2959

'`all_df` - Comparison of all Models'

user_idx  item_idx item_id  WMF_123_score  WMF_456_score  WMF_789_score  \
0         0         0     381       2.110018       3.753257       3.692900   
1         0         1     602       0.807434      -0.628530      -0.064267   
2         0         2     431       1.648493       1.840384       1.829896   
3         0         3     875       0.449601      -0.720735      -0.495614   
4         0         4     182       1.758965       1.308895       0.883930   

   WMF_888_score  WMF_999_score  Linear Regression Prediction  \
0       3.763934       3.974546                      4.677530   
1      -0.289080      -0.587279                     -0.702605   
2       1.870474       1.534385                      1.836190   
3      -0.023751       0.247162                      0.148879   
4       1.706282       0.328557                      0.642075   

   Random Forest Score  BPR_score  WMF_score  Borda Count  Enhanced WMF Model  
0                 1.08   3.014429   2.056086          486                4052  
1                 1.38   2.702705   2.265926         2291                2094  
2                 1.00  -0.207694   1.055882         1942                5447  
3                 1.00  -3.052034  -1.497697         1059                4574  
4                 1.40  -0.414165   0.173729          615                2959

Now that we have all model scores in the same table. Let's calculate the same **Precision@K** AND **Recall@K** values as run in the experiments.

We do this by manually calculating recall values with the respective formulas.

In [63]:
models = ["BPR_score", "WMF_score", "Borda Count", "Enhanced WMF Model", "Linear Regression Prediction", "Random Forest Score"]
result_df = {
    "Model": models,
    f"Precision@{TOPK}": [],
    f"Recall@{TOPK}": []
}
test_users = set(test_set.uir_tuple[0])
for model in tqdm(models):
    all_df = all_df.sort_values(model, ascending=False) # sort by predicted ratings
    predicted_ids = [all_df[all_df['user_idx'] == uidx]['item_idx'].values[:TOPK].astype(int) for uidx in range(train_set.num_users)]
    precisions, recalls = [], []
    
    for uidx in test_users:
        true_top_k = test_set.user_data[uidx][0] # ground truth data
        predicted_top_k = predicted_ids[uidx].tolist() # predicted ranking data
        # precision@K
        precision = len(set(true_top_k) & set(predicted_top_k)) / len(predicted_top_k)
        precisions.append(precision)
        #recall@K
        recall = len(set(true_top_k) & set(predicted_top_k)) / len(true_top_k)
        recalls.append(recall)

    result_df[f"Precision@{TOPK}"].append(np.mean(precisions))
    result_df[f"Recall@{TOPK}"].append(np.mean(recalls))

display(pd.DataFrame(result_df))

100%|██████████| 6/6 [00:05<00:00,  1.18it/s]


Model  Precision@50  Recall@50
0                     BPR_score      0.014340   0.035310
1                     WMF_score      0.014851   0.036007
2                   Borda Count      0.014979   0.035099
3            Enhanced WMF Model      0.015617   0.036940
4  Linear Regression Prediction      0.077766   0.315686
5           Random Forest Score      0.019681   0.053875

Based on the results, we can see that the Borda Count model has the highest Precision@50 and Recall@50.

However, there is no one model that is the 'ideal' model for all datasets and scenarios.
Depending on the dataset, different models may perform better than others.

---

Therefore, it is important to experiment with different models and ensemble methods to find the best model for a specific dataset and scenario.

Continue experimenting with different models and ensemble methods to find the best model for your specific dataset and scenario. Have fun experimenting!